In [ ]:
import numpy as np
loudness_data_n7 = np.array([np.nan,np.nan,np.nan,np.nan,-0.305792,-0.105102,0.183129,0.265712,0.627094,0.724554,1.015205,1.132958,1.725353,1.697663,1.814931,1.891386,2.309499,2.465781,2.630860])
loudness_data_n6 = np.array([np.nan,np.nan,np.nan,np.nan,np.nan,-1.084213,-0.678818,-0.602983,-0.203698,0.110290,0.531146,0.989981,1.062504,1.391716,1.478321,1.598163,1.779723,2.019546,2.297004])
loudness_data_n5 = np.array([np.nan,np.nan,-0.663247,-0.135962,0.055655,0.136097,0.516276,0.776163,0.859717,0.739199,1.114550,1.283773,1.146815,1.214429,1.605921,1.819364,1.927476,2.032690,2.031693])
loudness_data_n4 = np.array([np.nan,np.nan,np.nan,np.nan,np.nan,-0.161520,0.300446,0.502216,0.559076,0.654683,0.955243,0.968337,0.885020,0.965291,1.290606,1.397530,1.460671,1.729242,1.781090])
loudness_data_n3 = np.array([np.nan,np.nan,np.nan,np.nan,-0.634546,-0.649037,-0.492980,-0.365368,-0.002425,0.104951,0.144388,0.318761,0.540428,0.655482, 0.994505, 0.934209,1.060224, 1.293006,1.501077])
loudness_data_n2 = np.array([np.nan,np.nan,np.nan,np.nan,np.nan,np.nan,np.nan,-0.767364,-0.476870,-0.193201,0.078374,0.172603,0.419829,0.500441,0.720262,0.920215,1.080807,1.295526,1.501556])
loudness_data_n1 = np.array([-0.669534,-0.546282,-0.546282,-0.671033,-0.683743,-0.147340,0.084086,0.203489,0.461973,0.421456,0.525431,0.691075,0.733513,0.761766,1.076224,1.245589,1.340460,1.642738,1.773085])

In [ ]:
import numpy as np
#%EWT functions
def ewt_vineet(f,boundaries):
    # signal spectrum
    ff = np.fft.fft(f)
    ff = abs(ff[0:int(np.ceil(ff.size / 2))])  # one-sided magnitude

    #extend the signal by mirroring to deal with boundaries
    ltemp = int(np.ceil(f.size/2)) #to behave the same as matlab's round
    fMirr =  np.append(np.flip(f[0:ltemp-1],axis = 0),f)
    fMirr = np.append(fMirr,np.flip(f[-ltemp-1:-1],axis = 0))
    ffMirr = np.fft.fft(fMirr)
    # build the corresponding filter bank
    mfb = EWT_Meyer_FilterBank(boundaries, ffMirr.size)

    # filter the signal to extract each subband
    ewt = np.zeros(mfb.shape)
    for k in range(mfb.shape[1]):
        ewt[:, k] = np.real(np.fft.ifft(np.conjugate(mfb[:, k]) * ffMirr))
    ewt = ewt[ltemp - 1:-ltemp, :]

    return ewt


def EWT_Meyer_FilterBank(boundaries, Nsig):
    """
     =========================================================================
     function mfb=EWT_Meyer_FilterBank(boundaries,Nsig)

     This function generate the filter bank (scaling function + wavelets)
     corresponding to the provided set of frequency segments

     Input parameters:
       -boundaries: vector containing the boundaries of frequency segments (0
                    and pi must NOT be in this vector)
       -Nsig: signal length

     Output:
       -mfb: cell containing each filter (in the Fourier domain), the scaling
             function comes first and then the successive wavelets

     Author: Jerome Gilles
     Institution: UCLA - Department of Mathematics
     Year: 2012
     Version: 1.0

     Python Version: Vinícius Rezende Carvalho - vrcarva@ufmg.br
     Universidade Federal de Minas Gerais - Brasil
     Núcleo de Neurociências
     =========================================================================
     """
    Npic = len(boundaries)
    # compute gamma
    gamma = 1
    for k in range(Npic - 1):
        r = (boundaries[k + 1] - boundaries[k]) / (boundaries[k + 1] + boundaries[k])
        if r < gamma:
            gamma = r
    r = (np.pi - boundaries[Npic - 1]) / (np.pi + boundaries[Npic - 1])
    if r < gamma:
        gamma = r
    gamma = (1 - 1 / Nsig) * gamma  # this ensure that gamma is chosen as strictly less than the min

    mfb = np.zeros([Nsig, Npic + 1])

    # EWT_Meyer_Scaling
    Mi = int(np.floor(Nsig / 2))
    w = np.fft.fftshift(np.linspace(0, 2 * np.pi - 2 * np.pi / Nsig, num=Nsig))
    w[0:Mi] = -2 * np.pi + w[0:Mi]
    aw = abs(w)
    yms = np.zeros(Nsig)
    an = 1. / (2 * gamma * boundaries[0])
    pbn = (1. + gamma) * boundaries[0]
    mbn = (1. - gamma) * boundaries[0]
    for k in range(Nsig):
        if aw[k] <= mbn:
            yms[k] = 1
        elif ((aw[k] >= mbn) and (aw[k] <= pbn)):
            yms[k] = np.cos(np.pi * EWT_beta(an * (aw[k] - mbn)) / 2)
    yms = np.fft.ifftshift(yms)
    mfb[:, 0] = yms

    # generate rest of the wavelets
    for k in range(Npic - 1):
        mfb[:, k + 1] = EWT_Meyer_Wavelet(boundaries[k], boundaries[k + 1], gamma, Nsig)

    mfb[:, Npic] = EWT_Meyer_Wavelet(boundaries[Npic - 1], np.pi, gamma, Nsig)

    return mfb
def EWT_beta(x):
    """
    Beta = EWT_beta(x)
    function used in the construction of Meyer's wavelet
    """
    if x<0:
        bm=0
    elif x>1:
        bm=1
    else:
        bm=(x**4)*(35.-84.*x+70.*(x**2)-20.*(x**3))
    return bm
def EWT_Meyer_Wavelet(wn,wm,gamma,Nsig):
    """
    =========================================================
    ymw=EWT_Meyer_Wavelet(wn,wm,gamma,N)
    
    Generate the 1D Meyer wavelet in the Fourier
    domain associated to scale segment [wn,wm] 
    with transition ratio gamma
    
    Input parameters:
      -wn : lower boundary
      -wm : upper boundary
      -gamma : transition ratio
      -N : number of point in the vector
    
    Output:
      -ymw: Fourier transform of the wavelet on the band [wn,wm]
    Author: Jerome Gilles
    Institution: UCLA - Department of Mathematics
    Year: 2012
    Version: 1.0
    
    Python Version: Vinícius Rezende Carvalho - vrcarva@ufmg.br
    Universidade Federal de Minas Gerais - Brasil
    Núcleo de Neurociências 
    ==========================================================            
    """
    Mi=int(np.floor(Nsig/2))
    w=np.fft.fftshift(np.linspace(0,2*np.pi - 2*np.pi/Nsig,num = Nsig))
    w[0:Mi]=-2*np.pi+w[0:Mi]
    aw=abs(w)
    ymw=np.zeros(Nsig)
    an=1./(2*gamma*wn)
    am=1./(2*gamma*wm)
    pbn=(1.+gamma)*wn
    mbn=(1.-gamma)*wn
    pbm=(1.+gamma)*wm
    mbm=(1.-gamma)*wm

    for k in range(Nsig):
        if ((aw[k]>=pbn) and (aw[k]<=mbm)):
            ymw[k]=1
        elif ((aw[k]>=mbm) and (aw[k]<=pbm)):
            ymw[k]=np.cos(np.pi*EWT_beta(am*(aw[k]-mbm))/2)
        elif ((aw[k]>=mbn) and (aw[k]<=pbn)):
            ymw[k]=np.sin(np.pi*EWT_beta(an*(aw[k]-mbn))/2)
    ymw=np.fft.ifftshift(ymw)
    return ymw

In [ ]:
boundaries = np.array([0.63679854007417,1.24043747184364,1.90051054875325,2.19052315291591,2.42542041587323,2.62882317400665,2.76529989452493,2.88996614389811,3.01463240497312])
#                      0.661729806644950	1.31392423210288	2.01336596231180	2.34537159606571	2.51727971626241	2.65900552640622	2.78104721085925	2.90308890850569	3.02513061734896

# boundaries for F4 and F1 are similar, so the preset boundaries will be used.

In [ ]:
cd ..

/home/nitya/.local/share/Trash/files


In [ ]:
cd projects/LoudnessCurve(vineet)/

[Errno 2] No such file or directory: 'projects/LoudnessCurve(vineet)/'
/home/nitya/projects/LoudnessCurve(vineet)


In [ ]:
# EWT x,y computation for N1 F1
import os
import glob
import re
!unzip "resampled_dataset_f1_n1.zip"
os.chdir("resampled_dataset")
my_files = glob.glob('*.txt')
ewt_output = np.zeros(shape = (126,10,len(my_files)))
for i in range(0,len(my_files)):
  ewt_output[:,:,i] = ewt_vineet(np.loadtxt(my_files[i],delimiter = ','),boundaries)
np.save('/home/nitya/projects/LoudnessCurve(vineet)/x_n1',ewt_output)
y = np.zeros(len(my_files))
for i in range(len(my_files)):
  test_string = my_files[i]
  temp = re.findall(r'\d+', test_string)
  res = list(map(int, temp))
  loudness_level = int(res[-1])
  index = int((loudness_level/5)-2)
  y[i] =  loudness_data_n1[index]
np.save('/home/nitya/projects/LoudnessCurve(vineet)/y_n1',y)

Streaming output truncated to the last 5000 lines.
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_10.txt  
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_100.txt  
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_15.txt  
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_20.txt  
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_25.txt  
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_30.txt  
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_35.txt  
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_40.txt  
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_45.txt  
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_50.txt  
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_55.txt  
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_60.txt  
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_65.txt  
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_70.txt  
  inflating: resampled_dataset/F1_raw_N1_R3_cycle_216_75.txt  
  i

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_625_35.txt  
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_625_40.txt  
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_625_45.txt  
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_625_50.txt  
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_625_55.txt  
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_625_60.txt  
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_625_65.txt  
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_625_85.txt  
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_626_10.txt  
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_626_15.txt  
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_626_25.txt  
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_626_30.txt  
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_626_35.txt  
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_626_40.txt  
  inflating: resampled_dataset/F1_raw_N1_R8_cycle_626_45.txt  
  in

In [ ]:
cd ..

/home/nitya/projects/LoudnessCurve(vineet)


In [ ]:
# EWT x,y computation for N2 F1
import os
import glob
import re
!unzip "resampled_dataset_f1_n2.zip"
os.chdir("resampled_dataset_f1_n2")
my_files = glob.glob('*.txt')
ewt_output = np.zeros(shape = (126,10,len(my_files)))
for i in range(0,len(my_files)):
  ewt_output[:,:,i] = ewt_vineet(np.loadtxt(my_files[i],delimiter = ','),boundaries)
np.save('/home/nitya/projects/LoudnessCurve(vineet)/x_n2',ewt_output)
y = np.zeros(len(my_files))
for i in range(len(my_files)):
  test_string = my_files[i]
  temp = re.findall(r'\d+', test_string)
  res = list(map(int, temp))
  loudness_level = int(res[-1])
  index = int((loudness_level/5)-2)
  y[i] =  loudness_data_n2[index]
np.save('/home/nitya/projects/LoudnessCurve(vineet)/y_n2',y)

Streaming output truncated to the last 5000 lines.
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R3_cycle_763_50.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R3_cycle_763_55.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R3_cycle_763_60.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R3_cycle_763_65.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R3_cycle_763_70.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R3_cycle_763_75.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R3_cycle_763_80.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R3_cycle_763_85.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R3_cycle_763_90.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R3_cycle_763_95.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R3_cycle_764_100.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R3_cycle_764_40.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R3_cycle_764_45.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R3_c

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R8_cycle_625_55.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R8_cycle_625_60.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R8_cycle_625_65.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R8_cycle_625_70.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R8_cycle_625_75.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R8_cycle_625_80.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R8_cycle_625_85.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R8_cycle_625_95.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R8_cycle_626_100.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R8_cycle_626_40.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R8_cycle_626_45.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R8_cycle_626_50.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R8_cycle_626_55.txt  
  inflating: resampled_dataset_f1_n2/F1_raw_N2_R8_c

In [ ]:
cd ..

/home/nitya/projects/LoudnessCurve(vineet)


In [ ]:
# EWT x,y computation for N4 F1
import os
import glob
import re
!unzip "resampled_dataset_f1_n4.zip"
os.chdir("resampled_dataset_f1_n4")
my_files = glob.glob('*.txt')
ewt_output = np.zeros(shape = (126,10,len(my_files)))
for i in range(0,len(my_files)):
  ewt_output[:,:,i] = ewt_vineet(np.loadtxt(my_files[i],delimiter = ','),boundaries)
np.save('/home/nitya/projects/LoudnessCurve(vineet)/x_n4',ewt_output)
y = np.zeros(len(my_files))
for i in range(len(my_files)):
  test_string = my_files[i]
  temp = re.findall(r'\d+', test_string)
  res = list(map(int, temp))
  loudness_level = int(res[-1])
  index = int((loudness_level/5)-2)
  y[i] =  loudness_data_n4[index]
np.save('/home/nitya/projects/LoudnessCurve(vineet)/y_n4',y)

Streaming output truncated to the last 5000 lines.
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R3_cycle_469_55.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R3_cycle_469_60.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R3_cycle_469_65.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R3_cycle_469_70.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R3_cycle_469_75.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R3_cycle_469_80.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R3_cycle_469_85.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R3_cycle_469_90.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R3_cycle_469_95.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R3_cycle_46_100.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R3_cycle_46_30.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R3_cycle_46_35.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R3_cycle_46_40.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R3_cycle

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R8_cycle_357_55.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R8_cycle_357_60.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R8_cycle_358_30.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R8_cycle_358_35.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R8_cycle_358_40.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R8_cycle_358_45.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R8_cycle_358_50.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R8_cycle_358_55.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R8_cycle_358_60.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R8_cycle_359_30.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R8_cycle_359_35.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R8_cycle_359_40.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R8_cycle_359_45.txt  
  inflating: resampled_dataset_f1_n4/F1_raw_N4_R8_cy

In [ ]:
cd ..

/home/nitya/projects/LoudnessCurve(vineet)


In [ ]:
# EWT x,y computation for N5 F1
import os
import glob
import re
!unzip "resampled_dataset_f1_n5.zip"
os.chdir("resampled_dataset_f1_n5")
my_files = glob.glob('*.txt')
ewt_output = np.zeros(shape = (126,10,len(my_files)))
for i in range(0,len(my_files)):
  ewt_output[:,:,i] = ewt_vineet(np.loadtxt(my_files[i],delimiter = ','),boundaries)
np.save('/home/nitya/projects/LoudnessCurve(vineet)/x_n5',ewt_output)
y = np.zeros(len(my_files))
for i in range(len(my_files)):
  test_string = my_files[i]
  temp = re.findall(r'\d+', test_string)
  res = list(map(int, temp))
  loudness_level = int(res[-1])
  index = int((loudness_level/5)-2)
  y[i] =  loudness_data_n5[index]
np.save('/home/nitya/projects/LoudnessCurve(vineet)/y_n5',y)

Streaming output truncated to the last 5000 lines.
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R3_cycle_306_95.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R3_cycle_307_100.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R3_cycle_307_25.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R3_cycle_307_30.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R3_cycle_307_35.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R3_cycle_307_40.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R3_cycle_307_45.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R3_cycle_307_50.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R3_cycle_307_55.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R3_cycle_307_60.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R3_cycle_307_65.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R3_cycle_307_70.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R3_cycle_307_75.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R3_c

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R8_cycle_4_45.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R8_cycle_4_50.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R8_cycle_4_55.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R8_cycle_4_60.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R8_cycle_4_90.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R8_cycle_500_25.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R8_cycle_500_30.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R8_cycle_500_35.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R8_cycle_500_40.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R8_cycle_500_45.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R8_cycle_500_50.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R8_cycle_500_55.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R8_cycle_500_60.txt  
  inflating: resampled_dataset_f1_n5/F1_raw_N5_R8_cycle_500_90

In [ ]:
cd ..

/home/nitya/projects/LoudnessCurve(vineet)


In [ ]:
# EWT x,y computation for N6 F1
import os
import glob
import re
!unzip "resampled_dataset_f1_n6.zip"
os.chdir("resampled_dataset_f1_n6")
my_files = glob.glob('*.txt')
ewt_output = np.zeros(shape = (126,10,len(my_files)))
for i in range(0,len(my_files)):
  ewt_output[:,:,i] = ewt_vineet(np.loadtxt(my_files[i],delimiter = ','),boundaries)
np.save('/home/nitya/projects/LoudnessCurve(vineet)/x_n6',ewt_output)
y = np.zeros(len(my_files))
for i in range(len(my_files)):
  test_string = my_files[i]
  temp = re.findall(r'\d+', test_string)
  res = list(map(int, temp))
  loudness_level = int(res[-1])
  index = int((loudness_level/5)-2)
  y[i] =  loudness_data_n6[index]
np.save('/home/nitya/projects/LoudnessCurve(vineet)/y_n6',y)

Streaming output truncated to the last 5000 lines.
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R2_cycle_436_70.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R2_cycle_436_75.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R2_cycle_436_80.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R2_cycle_436_85.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R2_cycle_436_90.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R2_cycle_436_95.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R2_cycle_437_100.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R2_cycle_437_30.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R2_cycle_437_35.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R2_cycle_437_40.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R2_cycle_437_45.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R2_cycle_437_50.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R2_cycle_437_55.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R2_c

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R9_cycle_6_75.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R9_cycle_6_80.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R9_cycle_6_85.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R9_cycle_6_90.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R9_cycle_6_95.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R9_cycle_700_100.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R9_cycle_700_30.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R9_cycle_700_35.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R9_cycle_700_40.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R9_cycle_700_45.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R9_cycle_700_50.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R9_cycle_700_55.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R9_cycle_700_60.txt  
  inflating: resampled_dataset_f1_n6/F1_raw_N6_R9_cycle_700_6

In [ ]:
cd ..

/home/nitya/projects/LoudnessCurve(vineet)


In [ ]:
# EWT x,y computation for N7 F1
import os
import glob
import re
!unzip "resampled_dataset_f1_n7.zip"
os.chdir("resampled_dataset_f1_n7")
my_files = glob.glob('*.txt')
ewt_output = np.zeros(shape = (126,10,len(my_files)))
for i in range(0,len(my_files)):
  ewt_output[:,:,i] = ewt_vineet(np.loadtxt(my_files[i],delimiter = ','),boundaries)
np.save('/home/nitya/projects/LoudnessCurve(vineet)/x_n7',ewt_output)
y = np.zeros(len(my_files))
for i in range(len(my_files)):
  test_string = my_files[i]
  temp = re.findall(r'\d+', test_string)
  res = list(map(int, temp))
  loudness_level = int(res[-1])
  index = int((loudness_level/5)-2)
  y[i] =  loudness_data_n7[index]
np.save('/home/nitya/projects/LoudnessCurve(vineet)/y_n7',y)

Streaming output truncated to the last 5000 lines.
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R3_cycle_453_40.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R3_cycle_453_45.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R3_cycle_453_50.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R3_cycle_453_55.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R3_cycle_453_60.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R3_cycle_453_65.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R3_cycle_453_70.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R3_cycle_453_75.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R3_cycle_453_80.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R3_cycle_453_85.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R3_cycle_453_90.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R3_cycle_453_95.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R3_cycle_454_100.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R3_c

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R7_cycle_135_95.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R7_cycle_136_100.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R7_cycle_136_30.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R7_cycle_136_35.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R7_cycle_136_40.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R7_cycle_136_45.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R7_cycle_136_50.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R7_cycle_136_55.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R7_cycle_136_60.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R7_cycle_136_65.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R7_cycle_136_70.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R7_cycle_136_75.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R7_cycle_136_80.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R7_c

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R8_cycle_6_75.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R8_cycle_6_80.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R8_cycle_6_85.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R8_cycle_6_90.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R8_cycle_6_95.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R8_cycle_700_100.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R8_cycle_700_30.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R8_cycle_700_35.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R8_cycle_700_40.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R8_cycle_700_45.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R8_cycle_700_50.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R8_cycle_700_55.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R8_cycle_700_60.txt  
  inflating: resampled_dataset_f1_n7/F1_raw_N7_R8_cycle_700_6

In [ ]:
cd ..

/home/nitya/projects/LoudnessCurve(vineet)


In [ ]:
cd drive/

/content/drive


In [ ]:
ls

MyDrive/  Shareddrives/


In [ ]:
cd MyDrive

/content/drive/MyDrive


In [ ]:
ls

 0K2P2e1dc_5_raw.wav
 0K2P2e1dc_5.wav
'1(1) (1).gdoc'
'1(1) (1).pdf'
'1(1).gdoc'
'1(1).pdf'
 137.100_2020-01-28_16-59-15-1.wav
 137.620_2020-01-26_08-04-25.wav
 1575883319809.jpg
 16.pptx
'190002068 EE 203.pdf'
'190002068 EE 256.pdf'
'190002068_Vineet_Tripathi_EE (1).pdf'
'190002068_Vineet_Tripathi_EE (2).pdf'
'190002068_Vineet_Tripathi_EE (3).pdf'
'190002068_Vineet_Tripathi_EE (4).pdf'
'190002068_Vineet_Tripathi_EE (5).pdf'
'190002068_Vineet_Tripathi_EE (6).pdf'
'190002068_Vineet_Tripathi_EE (7).pdf'
 190002068_Vineet_Tripathi_EE.gdoc
 190002068_Vineet_Tripathi_EE.pdf
 190002068_VineetTripathi_endsem.pdf
 190002068_Vineet_Tripathi.pdf
 1998-AIComm.pdf
 20201101_182928.jpg
 4.2.gslides
 4.2.pptx
 4.pptx
 AllAlumni.xlsx
'Alumni 2020'/
'Alumni Association .gdoc'
'Alumni Cell.gsheet'
'Alumni Cell New Logo MC White Back.jpg'
'Alumni Cell New Logo TBWOS.png'
'Alumni Cell orientation.gslides'
'Alumni Cell recruitment.gform'
'Alumni Cell Report 19-20.gdoc'
'Alumni Cell.xlsx'
'Alumni Database 